# Загрузка необходимых данных
Для того, чтобы начать работать с программой, необходимо скачать словари на русском и украинском языке, которые переводят слова из языков в векторное совмещенное пространство. Для этого используем последующие две ячейки. Загрузка может быть не быстрой, наберитесь терпения.

In [ ]:
!wget https://s3.amazonaws.com/arrival/embeddings/wiki.multi.ru.vec --no-check-certificate

In [ ]:
!wget https://s3.amazonaws.com/arrival/embeddings/wiki.multi.uk.vec --no-check-certificate

In [3]:
# импортируем необходимые модули для работы со словарями
import io
import numpy as np
import unicodedata
import string
import re
import random
import codecs
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F



# Пишем пословный перевод
Данная часть программы пословно переводит предложения, используя простой русско-украинский словарь.

In [20]:
def unicodeToAscii(s):
    '''
    функция нормализует строки, 
    удаляя из них технические и ненужные
    нам символы кодировки unicode
    '''
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )

def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    return s.strip()

def normalizeString_cyr(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^а-яА-Я.!?]+", r" ", s)
    return s.strip()


# Загрузка пословных словарей
Загрузка из файлов, которые находятся в папке с ноутбуком.

In [77]:
def dict_download_ru(path):
    with open(path,'r',encoding='utf-8') as f:
        dict_lang2lang = {}
        for line in f:
            word = line.split(' ')
            if word[0] not in dict_lang2lang:
                dict_lang2lang[word[0]] = word[1].replace('\n','')
        return dict_lang2lang
    
def dict_download_uk(path):
    with open(path,'r',encoding='utf-8') as f:
        dict_lang2lang = {}
        for line in f:
            word = line.split('\t')
            if word[0] not in dict_lang2lang:
                dict_lang2lang[word[0]] = word[1].replace('\n','')
        return dict_lang2lang
    
def dict_merge(dict_ru2en,dict_en2uk): 
    dict_ru2uk = {}
    for k,v in dict_ru2en.items():
#         print(k,' ',v)
        if k not in dict_ru2uk:
            if dict_ru2en[k] in dict_en2uk:
                dict_ru2uk[k] = dict_en2uk[dict_ru2en[k]]
    return dict_ru2uk

In [82]:
#загружаем в локальную память и сливаем в русско-украинский словарь            
dict_ru2en = dict_download_ru('ru-en.txt')
dict_en2uk = dict_download_uk('en-uk.txt')
dict_ru2uk = dict_merge(dict_ru2en,dict_en2uk)

# выведем первые десять элементов, чтобы удостовериться, что создан хороший словарь  
counter = 0        
for a,b in dict_ru2uk.items():
    print(a,' ',b, counter)
    counter += 1
    if counter > 10:
        break


категория   категорія 0
что   що 1
для   для 2
как   як 3
был   був 4
его   його 5
также   також 6
это   цей 7
после   після 8
области   області 9
год   рік 10


In [79]:
len(dict_ru2uk.items())

27210

# функция перевода
пословный перевод, загружаем в функцию строку, она делит ее на слова и каждое слово переводит согласно существующему словарю
по дефолту загружен словарь англо-французский.

In [80]:
def translate(seq,dict_trans = dict_ru2uk):
    translated_string = ''
    word_list = seq.split(' ')
    for word in word_list:
        if word in dict_trans:
            translated_string = translated_string + dict_trans[word] + ' '
        else:
            translated_string = translated_string + word + ' '
    return translated_string

# можно добавить еще удаление синтаксиса(запятых и других символов)

In [81]:
print(translate('я тебя люблю твои папа и мама '))

я тобою любов твои тато и mama  


# Пословный перевод с помощью векторного словаря 

In [95]:
def load_vec(emb_path):
    vectors = []
    word2id = {}
    with io.open(emb_path, 'r', encoding='utf-8', newline='\n', errors='ignore') as f:
        
        counter = 0
        
        next(f)
        for i, line in enumerate(f):
            print(i)
            orig_word, vect = line.rstrip().split(' ', 1)
            word = normalizeString(orig_word)
            vect = np.fromstring(vect, sep=' ')
            
            counter += 1
            if counter > 10:
                break
                
                
            if word in word2id:
#                 print(u'word found twice: {0} ({1})'.format(word, orig_word))
                if orig_word==word:
                    id = word2id[word]
                    vectors[id] = vect
#                     print('rewriting')
                    continue
                else:
                    continue
            vectors.append(vect)
            word2id[word] = len(word2id)
            
    id2word = {v: k for k, v in word2id.items()}
    embeddings = np.vstack(vectors)
    return embeddings, id2word, word2id

In [25]:
def load_vec_2(emb_path):
    vectors = []
    word2id = {}
    with io.open(emb_path, 'r', encoding='utf-8', newline='\n', errors='ignore') as f:
        
        counter = 0
        
        next(f)
        for i, line in enumerate(f):
            words = line.rstrip().split(' ',1)
            print(normalizeString_cyr(words[0]))
            orig_word, vect = line.rstrip().split(' ', 1)
            word = normalizeString_cyr(orig_word)
            vect = np.fromstring(vect, sep=' ')
            
#             counter += 1
#             if counter > 10:
#                 break   
            if word in word2id:
#                 print(u'word found twice: {0} ({1})'.format(word, orig_word))
                if orig_word==word:
                    id = word2id[word]
                    vectors[id] = vect
#                     print('rewriting')
                    continue
                else:
                    continue
            vectors.append(vect)
            word2id[word] = len(word2id)
            
    id2word = {v: k for k, v in word2id.items()}
    embeddings = np.vstack(vectors)
    return embeddings, id2word, word2id

In [24]:
load_vec_2('./wiki.multi.ru.vec')



.
в



и
на

с


(array([[-0.0654528 ,  0.00981313,  0.0243369 , ...,  0.0287688 ,
          0.0666131 ,  0.0347981 ],
        [-0.0204289 , -0.0505275 ,  0.0456607 , ...,  0.103726  ,
         -0.089501  , -0.00388705],
        [-0.00222261, -0.111317  ,  0.00685308, ...,  0.0176286 ,
         -0.00876105, -0.00398831],
        [ 0.0616866 ,  0.0109087 , -0.0173823 , ...,  0.046982  ,
          0.030698  , -0.0235388 ],
        [-0.017659  ,  0.0468123 , -0.0334445 , ...,  0.0448771 ,
         -0.0216986 , -0.0430939 ]]),
 {0: '', 1: '.', 2: 'в', 3: 'и', 4: 'на'},
 {'': 0, '.': 1, 'в': 2, 'и': 3, 'на': 4})

In [26]:
ru_embedding_tuple = load_vec_2('./wiki.multi.ru.vec')
print('align-vectored russian dictionary downloaded into memory')



.
в



и
на

с

по
категория
не

года

из
а
что
к
году
для
как
от

за
был
о
его
он
до
также
это
но
то

?
при
или
я
после
области
у
во
год
было
время

состав
была
же
так
место
были
м
раион
вид
перенаправление

раиона

под
их

россии
если
только
есть
ее
и
язык
ссср
раионе
код
более

мая
дата
г
ноября
деревня
где
со
января
марта
декабря
все
августа
является
том
октября

сентября
статьи
июля
уже
июня
апреля
сша
которыи
название
поселение
человек
смерти
лет
февраля
они
того
города
см
может
она
г
!
воины
можно
когда
однако
этого
которые

высота
нет
бы
этом
переписи
село
таблице


еще
н
т
быть
чтобы
стал
статья
вы
род
е


один
без
реки
между
статус
населения
саита
вп
годы

через
центра
х

национальныи

область
список

об
сельское
саит
века

официальныи
часть
против
этот
будет
несколько

п
которых
город
мира
д
первое
других
тем
де
чем
им
части
описание

всего
первыи
телефонныи
среди
фаил
карты

два
всех
раз
там
около
них
территории
второи
составе
например
очень
главы

км
карта
площадь
все
эт

жил
начиная
номинации
пожалуиста
петрович
международныи
называется
происхождения
январе
сами
министра
состоянию
вроде
минимальная
сыграл
взгляд
памяти
нарушение
куда
сделал
причем
странах
анатолии
своими
профиль
принимал
пример
администрации
ред

среднии
автора
президиума
мастер
европе
факты
ее
промышленности
уровень
деле
великого
русская
имели
бассеин
игрок
писатели
лауреат
случаях
удаления
среднеи
игорь
оба
значительно
средства
удалялась
украина
регионе
ряда
команду
реке
путем
такая
материалы
контракт
ведь
белоруссии
никаких
до н
приток
протекает
объектов
указом
сегодня
русское
солдат
линия
музея
официально
программа
научная
уезд
гвардии
советская

территория
власть
кпсс
славы
анна
призер
июле
команд
разные
штаба
фактически
пункта
умершие
сборник
ж

боях
месяцев
четырех
причине
растении
слева

языки
некоторое
раза
вокал
ними
группу
содержит
стать
озеро
периода
комиссии


дорога
монастырь
принято
газеты
доме

переулок
востоку
написано
немного
начали
защиты
форме
точно
скончался
широко

привело
крыма

западная
экспедиции
успех

открытие
полиции
ленинградскои
коммуны
физики
статуса
россии
цель
переименовать
обучение
кафедры
альма
личности
отправился
далеко
основу
писателя
оказывается
музыкальных


возраста
времен
персонажи
конфликта
вторых
остальных
европеиских
объем
южныи
картина
министерство
женился
материала
километров
семеиство
андерсон
покинул
занимается
казахстан

польскии
положения
круг
испания
начальником
высшего
умеренно
написана
окончательно
немецкого
предприятии
победа
крепость
федеральным
крым
возле
закона
парка
построики
жанр
ежегодно
хочет
кантона
самостоятельно
драмы
база
хочу
немецких
поддержки
сцене
леса
половины
которыми
общественныи
устья
использованием

городом
добавил
композиции
энергии
названа
данная
мартин
отставку
смысле
даваите
главная
местныи
краинеи
помочь
принимает
этапе
скорости
отказался
тысячи
погибли
арестован
принципе
мастера
абсолютно
екатерина
объединение
смысла
матер
командиром
рождении
прошли
большинства
бассеиновому
заняла
коммента

гражданская
лаборатории
заявку
выити
связана
написание
макс
кнр
появляются

представления
частных
планеты

золото
быстрого
венгрия
поколения
влияния
функции
древних
основано
австро
методов
малых
посольство
служит
известнои
франсуа
несколькими
мысли
активное
преступления
хуан

оригинальнои
самолеты
социальных
обществе
провел
способность
участвовать
восстановить
распространения
голова
туре
мотивам
переводчик
немецкие

правление
нтз
людям
миссии
исполнении
молдавии
способности
столько
случаино
обсуждать

коми
теплота
находит
корреспондент
архитекторы
реклама
ду
победителем
обзор
перевода
формулы
авиационного
газ
следующее
услуг
временно
пво
ночью
явление
села
использовании
соборе
главои
промышленность
старая
старых
руководителем
утверждения
огнем
советов
королевскои
хорватии
посмотреть
европеиского
красные

местнои
южном
возникает
камень

разумеется
футбольнои
приходит

час
романов
постановлением
леитенанта
ивановна
желание

костромскои
непонятно
привели
братом
называть
подготовке
посредс

живои
станцию
детская
анджелес
предыдущих
свято
указан
истока
учителя
релиз
падения

вначале
форт
событие
самим
основную
программное
рабочеи
редирект
сооружении
производству
ликвидации
принадлежат
джованни
армии
ответил
иные
жертв
подобное
медицинского
юстиции
пи
летчик
общих
оценке
шасси
числом
звучит
разработку
часовня
неделя
болгария
невского
возрождения
пенсионерами
гл
будущее
наследие
предполагается
носитель
отсутствии
подготовку
остается
освобождение

небольшая
последнем
кафедре

стефан
товаров
девушки
рыб
мемориальная
рекомендации
городская
словакии
горныи
музеи
медицинскии
оси
дерева
яндекс
постановление
решить
коста
диплом
саитов
коллекция
нии
назначение
ислам
предметов
аргентина
встреча
таврическои
адам
внешние
зала
всемирного
молодежнои
распространены
научным
отряды
реалов
выражение
ресурсы

разным
нации

молодого
жилои
среднее
креисер
границах
электронная
исследователь
хоккеисты
военном
конфликты
важную
внизу
двигателеи
десятки
ответа
комедии
буква
квартира
взгляды
соглашен

...

суоярвскии
адептами
невои
евгеники
смекалку
броком
тартуская

выраженному
сионистские
отраслевым
обратимых

экранирования
баккара
проталкиванием
выпрямители
залогиниться
благоустроенные
глазах

бех
межамериканского
самоопределению
должанском

снабжала
дальма
обустраивать

прудникова
марбургском
июльском
татьяновка
шуиская
выговорить
гудзь
сузах
веронскии
картинг
погонь
минеева
элиана
включенном
стокгольмская
интерлеикина
велосипедиста

порогового
монархистом
избранных
враждебностью
вывозом
нарастающим
креолов
попова
изгнанным

амплитуднои
красноярск
огорожен
панорамнои
багдасаров
бриллиантом
гулькина
снаиперами
замороженном
р к

окольничим
абраменко
мигом
шенка
буркхардт
полиграфическое
урмии
кусанаги
диомеда
сагами
пудость
языком
офтопик

цаплин
марисоль
шэньяна
даръа
стеклозавод

негласнои
летописцем
мюрреи
онтологическии
григорьево
евстратов
бердышев
гном
жетулиу
ситкомов
доминике
фрелунда
богдановского

емильчинского
общечеловеческои
похоронив


калье
животворящии
ровера
харкер
зар

хоби
иосси

размещенную
дублеров
квасников
маркандея
уругваицев
хорс
обмундированием
выиграннои
жувентуде
кальвинистскои
нигилизма
кексгольмскии
городца
рогань
букв
сущность
обозе

школьницеи
альбомного

погнался
зашифрованном
кеин
швыряет

обезглавить
волеренга
анестезиеи
южноосетинского

классифицироваться
форсаже
межотраслевого
актина

оштрафованы
буши
пиратскую

ангарска
бунд
бесплатен
белухи
созывались
украсила
мочевыделительнои
неевклидовои
братишка
летоисчисления
посредственные

тетиевскии
твэлов
иносказательно
маскирует
одномерныи
кричала
возрастании
ветрогенераторов
похвалила
костромским

чудныи
долиновка
херсон
либаво
малоазииских

бузонвиль

прерывал
раус
делфте
хрупкого
инара
овер
княжевич
антоник
пэк
этическую
кашкина
америкэн

моргаушскии

филаретов
североморске
хамсе
ярые
буерак
наросты
инфицированные
археографы

асадуллин
гегелевскои
машгиз


пробегов
горшков
приполярнои
солидном
лаинотт

программе
екатериновского

вампирша
закаев
блюхер
головогрудь

кадди
пироговскои
п

сложившемся
ревякино
лохвицкая

гугление
внешкольнои
мастацтва
бампером
захлестнула
предсерииных
сверхсрочную
взявшие
эшториле
ласточек
темпу

общегосударственнои
ермолинскии
монашествующие

понравившиеся
фландрская
тсуга
калорииность
мнении
благов
приобретет
раздражающим
ренн
архидиоцеза
чужеродные
ментенон
прутскии

взявших
отложила
отступавшими
эвтаназия
леонтовича
окаменевшие


думы
гавриш
формируемые
раззак
выставленным
бобр
соме
кореица
сумкои
гидрографическии
недостроенная
бержерон
кунст
амбри
миланская
проваливаются
шурф
распознаванию
дачами
вату
неумышленно
неореализм
переименует
плутино


хроматическои
кальциевые
подарок
вооружениями
монаршего
ильичевца

юристу
артемово

межевание
расплавленнои
торфяники
эллипсоидальные
телеграфным
галланд
распределенными
лэдд
лозово

припискои
широкино
завязаны
побережье
автобиографиеи
вегетарианская
поляковскии
эпифитное
вещественныи
акжаиык
караганду
повешенных
тансыккужина
высоцкого
мелодичного
альбинос
ацил


ходатаиствовали
бестях
внезе


высотном
прагматика
каитагского

хьюман
клиновидно
арбалеты

коптских


неразумныи
граничная
врятли
канури
валуево
фаилового
до
объединениях

диморфизмом
испаноязычная
выделяющаяся
дэвы


андрушевскии
юрьевны
прудовка
каинозоя
бомбардирами
зеиском
спицына
тростниковая
фигура
зенитчики
обрабатываемого
обнажая
отсылая
лазаревская
сесото
сошлюсь
щелочная

гранадскии
узурпаторы
калининградском
беркова
пожарам
списочного
колхозником
татрах
бгуир
суммарных
пронести
ссп
аннигиляции
фавор

пушкинскую
офицеры
ливиу
опережали
педра
флажками
малолетнему
патаки

филевская
фаиз

джаба

милосердию
благодарят
егорович
приподнятои
троллеибус

антивоенного
цаньцзюньши

клонах
непредсказуемые
мифа
несению
монтехо
тамми
золотников
сидоровская
выдержках
киммо
лориискои
шаику

сунского
мазурском
морра
эмиссаров
италии
густов
балалаике
ряван
сааре
рабынеи
тэхн ка
паулино
огвумике

моравские
мустамяэ
баженово
линденау
остравы
питкярантского
методички
остоя
надпоименнои
фантомс
месягутово
укладывать
посту
ка

золотника
тихоокеанскую
гарди
покинутои

лобковиц
стахановцев
франкоканадцы

барские
консультативную
пук
небесам
винкельхок
кириченко
астара
максимы
умножении
дубяго
пересмешница
дон
юнусович

вик
антаблемент
константиновне
хранительницеи
геллеспонт
батман
невнимателен
иулиана
саммиты
захоронения
предписаниями
исландским
нтуу

добровеличковском
оплачено
охотники
кхмерском
земскому
бие
подпольщикам
рсхд
бусин
подстраницами

организовываются
тросна
трофические
сабино
бретонских
разорванные
тонн
форинтов
извлекая
сокращениям
агванк
теилза
быка
водворения
пионир
коррумпированного
ветеранах
ромсдал
повислая
флакка

дятьковского
брасса
жнецы

разделенную
ельцине
виноградовои
многостороннего
роан
автомашина
гагика
базисные
тюменскую
извилина

асса
высокопольныи
незнакомцев
мензелинск
канадо
перечитывал

брунс
сарскии
чупа
шихматов
монетно
кормилицы
фатха
дефектных
долинская
align-vectored russian dictionary downloaded into memory


In [ ]:
uk_embedding_tuple = load_vec_2('./wiki.multi.uk.vec')
print('align-vectored ukranian dictionary downloaded into memory')


.





в

у
на

з
категор я
та
до
за

що
року
не
в д
а
для



також
як
р

роц
с
про
иого
м


укра ни
був

населення
и
було
в н
п д
по

це
км
п сля
або
час
з
але
област
як
при
де
о

я
якии

була
були
ос б
м ста

рок в
див
село
раион


об
раиону
через

п



перенаправлення
села
так
тому

р к
к
в дстань
ради
?
х
н
сша
ма

т
пам
яких
область
того
яка
вони

ж
ст
ще
саит
близько
в ини
цього

фаил
чи

м ж
роки
обговорення
коли
вона
х
лише


з
список
може

вересня
цеи
складу

березня
м сце
б
мун ципал тет
укра н

серпня
с чня
став
травня
грудня
нших

жовтня
серед
е
пкс
якщо
один

липня

участь
вид
можна
червня
м

них
м сто
вже
життя
срср
!
кв тня
сел

листопада
склад
лютого

и
опис
центр
г
зах д
т льки
франц
щоб


бути
стол ття
рада



в дстан


сх д
статт
склад
м н
особи
то
над
стор я
зображення
св ту
пункти

зв
територ

го
код
саит
разом
нш
проти
укра нсько

тут
укра нськии
раион
початку
мова
одного
населен
д
стор
якого
департаменту

вс
цьому
роках
багато
б льше

к льк сть
нституту
шаблони


с льсько
п вдн
рамках
одн
використовувати
раиони
менш
засновании

така
вибор в
озера
б льшост
батька
во
м г
середня

унр
виступ в
ту
дн
поняття
композитор
такого
працювати
молод
бою
результати
в дкрито
використовуються
яна
рос
м сць
електронна
правила
грав
матчах
вл тку
швец
творчост
участ
матер ал в
кра н
операц я
музики
пункт
м жнародних
кра на

лен на
напрямку
музе
львова
створении
с льське
нтернет
трохи
грец
спан я

призначення
родин
починаючи
п сня
том
укра нц в
острова
м н стра
обрании
позиц
лауреат

чотирьох
якою
червоно
рср
наступн

острови
голи
виходу
сина
к лькох
енциклопед я
науков
ком с
альбому
аль
да
крим
верс
селища
пов т
влада
здобув
депутат
числа

положення
криму
кожного
народно
поля
систему
м н стерства
створена
трет и
користувач
р чц
пост ино
заима
чолов к в
н чого
н меччина
зах дн и
п вн чно
володимира
н и
економ ки
палац
стад он
ж нки
м н стр в
газети
зробив
петра
чергу
родина
сх дн и
золота
ход
сторичн
окрем
будуть
радянська
язок
б бл отеки

уже
пов тря
загальному


польсько
значну
вс и
нижня
визнача ться
неодноразово
обслуговування
проект в
басеину
склав
в тал и
цвинтар
уваги
групу
б ла
с льськ
власн
православно
кордон
ртутно
тв р
м сцев
останн м
дея
клуб в
вимоги
типи
видиму
веде
стосовно
княз вства
почеснии
хн
б лецькии
завдовжки

л тератур
боях
казахстан
тисяч
червона
дентиф катора
вважа
короткии
ншо

провулок
зон
причини
проводиться
пере хав
степан
прац вник в
вид вел
вре в
америц
конструкц
наказом
метро
побудовании
прим тки
роками
сад
н ч
н мецька
окупац
манганова
заходи

марк
их
впродовж
вища
л кар
наиб льша
пар
лев
валер и
силу
довгии
конфес инии
дн пропетровсько
драми
польоту
зм
заима ться
богородиц
споруд
наст льки

снувала
слави
вся
перетворення
власност
реал зац
значимост

боротьб
газ
аеропорт
р
верс ю
здатн сть

костел
геро в
жили
зал знична
альпи
соц ально
генерала
англ исько
ж нка
д исно
португал
дочка
в домого
назад
кра ною
пост
органи
хвороби
чимало
процеси
прис лок
книгу
спадщини
тиску


дн пра
продукт в
наступних
б льшу
угоди
пр

середовище
британсько
бронзовии

створювати
долин
сторон
персонаж в
проф
змогу
дво
технолог я
планування
формат
папа
вмс
захищав
р чард
соф я
фр др х
селищ
маистр в
визначити
опору
лля
польська
префектури
п вострова
зроста
шлюб
грудень
моделеи
частка
царства
напис
автоматично
колекц
магдебурзьке
обрано
приинятии
проводяться
власного
п дтриму
дають
тал иськ
металу

дось
невелика
шлях в
московськии
березень
нашого
старшого
обличчя
складаються
р чнии
стор ччя
зразок
сут
концерт
язниц
корол вського
п вдня
вир шили
ув ишла
силою
зазнав
техн чнии
сцен

редагувань
р зко
золото
римськии
встановлении
само
характеристика
шляхи
липень
вноч
берега
козаки
микола вська
десь
сп вроб тник в
складалася
росте
серб
су
пан
деякими
аргентини
заимав
користувач
но
прямо
матчу
храми
написати
марки
арх тектора
литви
зустр ч
жити
коледж
арм ю
указ
д аметр
валентина
покарання
дозволило
занадто
становище
медалями
звичаинии
поч
загальною
заради
бачу
ф рма
попередник
переходу
продукти
бо в
ншою
поширении
снувало
гр



виишло
перебувала
символи
бавар
кр зь
нд я
вес лля
суден
густина
сиб ру
органами
проживають
командував

експлуатац ю
складова
собор
активних
елементами
диного
голодомору
н як
конференц я
перекладу
стверджу
зазнали
режисером
ведуть
рег онах

королева
школах
монета
будови
со
математичних
мом
р зновид
продукт
формули
нал чу
британська
дух
гипет
помилок
готель
сучасне
новини
я
м нськ
космос
споруда
ки вськ и
фрн
кул
вчитель
страны
вадим
корисн
дитини
встановив

свобода
внутр шн
заступника
критик в
леибл
энциклопедическии
коеф ц нт
колективи
виити
правах
представниками
верхн
головував
конго
молода
сутт во
в дбулась
черкаська
диск
русь
орган зац ю
академ ка
в дтак
арденни
наказав
сона
м сцевии
хуан
зберегти
кер вник в
душу
молодь
буд влю
р вне
м д
зм цнення
композитори
другою
японська
особливии
прага
в кна
семен
потрапля
укра нки
квт
нац ональним
алгоритм
р г

звании
позиц и
останню
дем
норм
зовн шньо
коду
мистецтв
поляк в
андерсон
воював
потрапили
худоби
склала
атмосфера
д яти
основно
пр


...

нов тня
зд иснювала
обаб ч
блискуче

в дм нн стю
борисова
пекла

автомати
побажання
бавар я
козловськии
молочнии
прадеш
юриста
систематика
жовтневии
прикладна
людина
б льшими
малюнком
публ цисти
тимчасових
властива
граф чного
вчинок
правопорядку

хорватського
ов
з ткнень
кип ння
переробц
грашки
бондарчук
маистерно
операц ю

ут к
тичини
флеити
близнюки
к
спорудили
гарячих
карбону
почув
кремн ю
лу са
засн
в дновленням
космонавтики
борис вна
воротами
трибуни
полковники

бо ться
паломництва
винятки
правильне
спину
енергетично
обирали
абатства
тп

кардинально


прихожан
померти
шотландсько
федер ко
лондонськии
сп в снують

бреш я
харг та
м на
васильк вського
колекц ях
ф з
старослов
розр з
навчаючись
визнавав
в тчизни
аркуш
електро
запахом
вропеиською
ланкою
бельг иського
тя
критичного
тал ць
пресс


нерв в
старовиннии
спанськ и
дмитр вка
р
ссср
оскара
собори
акторську

традиц иному
кольорами

досягнув
денного
бредл
човн
струн
кв нт
глибше
кубки
советскои
тактико
блокади
антонова
слава

дина


матер альна

носило
есм нець
розд льн сть
слон
вказали
тонкого
поганого
см ливо

шлезв г
в нченцо
земства
грецьке
географи

каннського
класик в
н дерландського

армия
розпочата
молочних
судилося
рузвельт
пластин

обробкою
едвардс
л нда
конотопськии
нституц и
розмову
неитрон в
в ков
дубляж
вивчала
протилежнии
вирушила
кр ст ана
льодовики
франкфурт
ню
нарад
бик
медичн и

морфолог
хал фату
переноситься
товарами
справедливо

лац о
ф л пп нах
початки
структурна
блага
к нно
династ ю

л карень
доручень
джазу
в домство
корадо
л тальних
генеральному
шепет вка
фентез ин
розрахован

перськ и
к нотеатру
вестибюль

гранат
секти
воротарем
театральн и
ятку
ни
нду зму

собрание
нду зм
туман

пласту
безпосередн
тоттенгем
п за
русалима
м цкевича
дуету
мультсер алу

самовизначення
георг вна
кислотою
корану
вулкан чного
квартал в
гастролював
рецепт
походили
тип центра
зачаття
д дусь
нво
хетчбек
швед
юрисдикц ю
троянди
урср

границя

присутн м
ол мп иським

мальме
сталевих
аромат
сн
митнии
скорочена

спод


рев з
дроту
буша
зра льськ
наставник
саут
дарв н
еи
зверта
л кувальн
глибоку
джош
перспектив
руслана
пруссько
смерти
наруто
смартфон
службу
торрес
плач
матчем

с нлун
англ ицями
виборола
есу
заимаючи
сус дньо
вза мопов
ф зичному
по днанням
димитр я
паном
гамбурз
по дну ться
румунською
резервного
наиближче
юв леинии
стратег чнии
сум сност
микола вськ и
працями
наистар шим
вертикальна
султаном
л верпуля

народжуються
набряк

давньорусько

тольятт
промову
вогнища
терен
урал
бюлетен в
алюм н и
язковими
зм нюючи
приб чники
бол
пров нц ями
коротко
митних
переведен
ор нтац ю
археолог в

ми
дельт
поморського
зростав
афанас и
долею
са д
ф ларет
вибухов
сеидж
велич
касерес
параметром
сквер

висадка
спалахнуло
надходили
програм ст
п двищеною
народ в
впевнен
впатор я
принс п
променями
канаду
величност
пережили

старими
задуму
сл дчого
земсько
в зант ю
нащадком

ф лол
човнах
чужии
стаж
пров дною
с льськогосподарську
молдовського
сталися
н гер
нижчии
уявленнями
пол гон
морав я
ка р
колег ум
деталям

просимо
хижаки
п двищують
престол

цифрами
ростом
катя
документальна
холери
римсько
костюм в
стотних
кулею
ф л и
мон ка
неповнии
поперечних
готуються
розм тки
референдум

подол
тод шн х

зубами

херсонськ и

стипенд
непорозум ння
третин
ч ткого
посередництва
ланцетн
бернардо
иордан я
в дпов ддю
альма
концепц ю
китаиц в
колон ями
оприлюднив
тисячами
сенатор в
сво р дною
цюрих

робилися
мун тет
вагона
значимою
леви
захищении
вуг лл
естафет
резервнии

леибли
частими
орлова
дубовии
переробку
пол мер в
никифорович
гн ту
товариськ и
слюсарем

вовни
кр са
д лових
вознесенськии
вар антами


образа
стр лецьк
ол мп я
печерська
рика
купи
президентства
незначнии
л ричн
кабел
терен
заимало
смертеи
тв и


докторська
всеволода
вибачення

стверджуючи
довш
рландсько
маяк
чехов
домашньо
гетеборг
просту
темряв
борц в
додачу
досконалост
коновальця
сев ль
пояснювати

ростов
археологами
воррен
нож
ср
роже
натурал ст
вир внювання
м нне
короткою
наиближчо
функц онального
дн продзержинськ
епос
фазу
наступник



видобуто
викладали
л тературознавства
давидов
шевченк вська
батькам
л на
рекомендують
в докремлю
мовчання
дво
тепловоз
панченко
кидк в
подв ино
компром с
краиова
васалом
техн ко
вл во
фарбою
вих дно
стокгольма
нормативн
краиня
мертвим
чуваська
сл дами
лежали
вад
в ртуальних
вернадськии
вокал стом
над ишов
нора
сааре
заселен
османи

спас
батум
аеромоб льна
антарктики
хан в
великомученика
абсурду
антон
близнюк в
навантаженням
монастирських
субота
потр инии
забудована
джерелознавства
при днании
щ льн стю
вген вна
крыма


приховании
никифор

подумати
надходити
проектна
к нцев
миргород
роботодавц в
моцарт
рнбо
пономарьов
обладунки
телефонних
фермерських
даг
невдалии
народ
католицизму
французами
ж у
розбудову
рудники
витриму
газова
всесоюзних
г мнасти
горобець
голосував
наир зноман тн ших

поглина
сигналом
г мном
джорджем
розташовувалась
душ
синтетичних
складову
мореплавець
буковини
чехословацько
порад
контролюють
реле
парт ин и
причетн сть
двором
листками
розвинуте
яскрав сть
х м к
волеибол

In [27]:
len(ru_embedding_tuple[0])

165844

In [28]:
ru_embedding_tuple[1]

{0: '',
 1: '.',
 2: 'в',
 3: 'и',
 4: 'на',
 5: 'с',
 6: 'по',
 7: 'категория',
 8: 'не',
 9: 'года',
 10: 'из',
 11: 'а',
 12: 'что',
 13: 'к',
 14: 'году',
 15: 'для',
 16: 'как',
 17: 'от',
 18: 'за',
 19: 'был',
 20: 'о',
 21: 'его',
 22: 'он',
 23: 'до',
 24: 'также',
 25: 'это',
 26: 'но',
 27: 'то',
 28: '?',
 29: 'при',
 30: 'или',
 31: 'я',
 32: 'после',
 33: 'области',
 34: 'у',
 35: 'во',
 36: 'год',
 37: 'было',
 38: 'время',
 39: 'состав',
 40: 'была',
 41: 'же',
 42: 'так',
 43: 'место',
 44: 'были',
 45: 'м',
 46: 'раион',
 47: 'вид',
 48: 'перенаправление',
 49: 'раиона',
 50: 'под',
 51: 'их',
 52: 'россии',
 53: 'если',
 54: 'только',
 55: 'есть',
 56: 'ее',
 57: 'язык',
 58: 'ссср',
 59: 'раионе',
 60: 'код',
 61: 'более',
 62: 'мая',
 63: 'дата',
 64: 'г',
 65: 'ноября',
 66: 'деревня',
 67: 'где',
 68: 'со',
 69: 'января',
 70: 'марта',
 71: 'декабря',
 72: 'все',
 73: 'августа',
 74: 'является',
 75: 'том',
 76: 'октября',
 77: 'сентября',
 78: 'статьи',
 79: 'ию

In [ ]:
def get_nn(word, src_emb, src_id2word, tgt_emb, tgt_id2word, K=5):
    print("Nearest neighbors of \"%s\":" % word)
    word2id = {v: k for k, v in src_id2word.items()}
    word_emb = src_emb[word2id[word]]
    scores = (tgt_emb / np.linalg.norm(tgt_emb, 2, 1)[:, None]).dot(word_emb / np.linalg.norm(word_emb))
    k_best = scores.argsort()[-K:][::-1]
    for i, idx in enumerate(k_best):
        print('%.4f - %s' % (scores[idx], tgt_id2word[idx]))

In [ ]:
for word in ['время','сайт','совета']:
    get_nn(word, ru_embedding_tuple[0], ru_embedding_tuple[1], uk_embedding_tuple[0], uk_embedding_tuple[1], K=3)

In [ ]:
word2id = {v: k for k, v in ru_embedding_tuple[1].items()}
word2id['время']

In [ ]:
#создание словаря англо-французского
# dict_en2fr = {}
# with open('en-fr.txt','r',encoding='utf-8' ) as f:
#     for line in f:
#         word = line.split(' ')
# #         for i in range(len(word)):
# #             print(word[i],end =' ')
#         if word[0] not in dict_en2fr:
#             dict_en2fr[word[0]] = word[1]
            
# #и франко-английского (если они разные)
# dict_fr2en = {}
# with open('fr-en.txt','r',encoding='utf-8' ) as f:
#     for line in f:
#         word = line.split(' ')
# #         for i in range(len(word)):
# #             print(word[i],end =' ')
#         if word[0] not in dict_en2fr:
#             dict_en2fr[word[0]] = word[1]